In [1]:
from tqdm import tqdm
import numpy as np
import torch
from torch.utils.data import DataLoader
import config

from datasets.aileen_object import AileenObjectDataset
from model import AttributeNetwork, VGG_Net, RES_Net

In [2]:
shapes = ['cone', 'box', 'cylinder', 'sphere', 'capsule']
sizes = ['small', 'medium', 'large']
colors = ['blue', 'red', 'green', 'yellow', 'purple']

testData = AileenObjectDataset(config.ROOT_TEST)
test_size = len(testData)
test_loader = DataLoader(dataset=testData, shuffle=False, batch_size=1)

In [3]:
model = VGG_Net(13)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
if torch.cuda.is_available():
    model.cuda()

In [4]:
print('Load weights...')
model.load_state_dict(torch.load('attribute_best_model.pth'))
print('Weights are loaded...')
model.to(device)

Load weights...
Weights are loaded...


VGG_Net(
  (main): VGG(
    (features): Sequential(
      (0): Conv2d(3, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (1): ReLU(inplace=True)
      (2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (3): ReLU(inplace=True)
      (4): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
      (5): Conv2d(64, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (6): ReLU(inplace=True)
      (7): Conv2d(128, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (8): ReLU(inplace=True)
      (9): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
      (10): Conv2d(128, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (11): ReLU(inplace=True)
      (12): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (13): ReLU(inplace=True)
      (14): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (15): ReLU(inplace=True)
      (16): M

In [5]:
def postprocess_attributes(pred):
    pred_shape = pred[0][0:5]
    pred_size = pred[0][5:8]
    pred_color = pred[0][8:13]
    index_max = np.where(pred_shape == np.max(pred_shape))[0][0]
    for i in range(len(pred_shape)):
        if i == index_max:
            pred_shape[index_max] = 1
        else:
            pred_shape[i] = 0
    index_max = np.where(pred_size == np.max(pred_size))[0][0]
    for i in range(len(pred_size)):
        if i == index_max:
            pred_size[index_max] = 1
        else:
            pred_size[i] = 0
    index_max = np.where(pred_color == np.max(pred_color))[0][0]
    for i in range(len(pred_color)):
        if i == index_max:
            pred_color[index_max] = 1
        else:
            pred_color[i] = 0
    pred[0][0:5] = pred_shape
    pred[0][5:8] = pred_size
    pred[0][8:13] = pred_color
    
    return pred

In [6]:
shape_correct = 0
size_correct = 0
color_correct = 0
curve_contour_acc = 0
edge_contour_acc = 0
plane_acc = 0
rect_plane_acc = 0
round_plane_acc = 0
with torch.no_grad():
    for x_batch, y_batch in tqdm(test_loader):
        x_batch, y_batch = x_batch.to(device), y_batch.to(device)
        y_test_pred = model(x_batch)
        # _, y_pred_tag = torch.max(y_test_pred, dim = 1)
        y_test_pred = y_test_pred.cpu().numpy().copy()
        y_test_pred = postprocess_attributes(y_test_pred)
        pred_shape = y_test_pred[0][0:5]
        pred_size = y_test_pred[0][5:8]
        pred_color = y_test_pred[0][8:13]
        
        
        pred_curve_contour = (y_test_pred[0][0] + y_test_pred[0][2] + y_test_pred[0][3] + y_test_pred[0][4]) > 0
        pred_edge_contour = (y_test_pred[0][0] + y_test_pred[0][1] + y_test_pred[0][2] + y_test_pred[0][4]) > 0
        pred_plane = (y_test_pred[0][0] + y_test_pred[0][1] + y_test_pred[0][2]) > 0
        pred_rect_plane = y_test_pred[0][1] > 0
        pred_round_plane = (y_test_pred[0][0] + y_test_pred[0][2]) > 0
        
        
        shape = shapes[np.where(pred_shape == np.max(pred_shape))[0][0]]
        size = sizes[np.where(pred_size == max(pred_size))[0][0]]
        color = colors[np.where(pred_color == max(pred_color))[0][0]]

        gt_y = y_batch.cpu().numpy().copy()
        gt_shape = gt_y[0][0:5]
        gt_size = gt_y[0][5:8]
        gt_color = gt_y[0][8:13]
        
        gt_curve_contour = (gt_y[0][0] + gt_y[0][2] + gt_y[0][3] + gt_y[0][4]) > 0
        gt_edge_contour = (gt_y[0][0] + gt_y[0][1] + gt_y[0][2] + gt_y[0][4]) > 0
        gt_plane = (gt_y[0][0] + gt_y[0][1] + gt_y[0][2]) > 0
        gt_rect_plane = gt_y[0][1] > 0
        gt_round_plane = (gt_y[0][0] + gt_y[0][2]) > 0
        
        # print gt_y
        # print np.where(gt_shape == np.max(gt_shape))
        gtshape = shapes[np.where(gt_shape == np.max(gt_shape))[0][0]]
        gtsize = sizes[np.where(gt_size == np.max(gt_size))[0][0]]
        gtcolor = colors[np.where(gt_color == np.max(gt_color))[0][0]]
        if shape == gtshape:
            shape_correct += 1
        if size == gtsize:
            size_correct += 1
        if color == gtcolor:
            color_correct += 1
        
        if pred_curve_contour == gt_curve_contour:
            curve_contour_acc += 1
        if pred_edge_contour == gt_edge_contour:
            edge_contour_acc += 1
        if pred_plane == gt_plane:
            plane_acc += 1
        if pred_rect_plane == gt_rect_plane:
            rect_plane_acc += 1
        if pred_round_plane == gt_round_plane:
            round_plane_acc += 1
        print("****************")
        print("predicted shape: %s    gt shape: %s" % (shape, gtshape))
        print("predicted size: %s    gt size: %s" % (size, gtsize))
        print("predicted color: %s    gt color: %s" % (color, gtcolor))
        print("predicted has_curve_contour: %r    gt has_curve_contour: %r" % (pred_curve_contour, gt_curve_contour))
        print("predicted has_edge_contour: %r    gt has_edge_contour: %r" % (pred_edge_contour, gt_edge_contour))
        print("predicted has_plane: %r    gt has_plane: %r" % (pred_edge_contour, gt_edge_contour))
        print("predicted has_rect_plane: %r    gt has_rect_plane: %r" % (pred_rect_plane, gt_rect_plane))
        print("predicted has_round_plane: %r    gt has_round_plane: %r" % (pred_round_plane, gt_round_plane))
        print("****************")

  0%|▏                                       | 27/7676 [00:00<00:59, 128.67it/s]

****************
predicted shape: sphere    gt shape: sphere
predicted size: medium    gt size: medium
predicted color: blue    gt color: blue
predicted has_curve_contour: True    gt has_curve_contour: True
predicted has_edge_contour: False    gt has_edge_contour: False
predicted has_plane: False    gt has_plane: False
predicted has_rect_plane: False    gt has_rect_plane: False
predicted has_round_plane: False    gt has_round_plane: False
****************
****************
predicted shape: sphere    gt shape: sphere
predicted size: medium    gt size: medium
predicted color: purple    gt color: purple
predicted has_curve_contour: True    gt has_curve_contour: True
predicted has_edge_contour: False    gt has_edge_contour: False
predicted has_plane: False    gt has_plane: False
predicted has_rect_plane: False    gt has_rect_plane: False
predicted has_round_plane: False    gt has_round_plane: False
****************
****************
predicted shape: box    gt shape: box
predicted size: mediu

  1%|▎                                       | 57/7676 [00:00<00:54, 140.36it/s]

****************
predicted shape: cylinder    gt shape: cylinder
predicted size: medium    gt size: medium
predicted color: purple    gt color: purple
predicted has_curve_contour: True    gt has_curve_contour: True
predicted has_edge_contour: True    gt has_edge_contour: True
predicted has_plane: True    gt has_plane: True
predicted has_rect_plane: False    gt has_rect_plane: False
predicted has_round_plane: True    gt has_round_plane: True
****************
****************
predicted shape: box    gt shape: box
predicted size: medium    gt size: medium
predicted color: blue    gt color: blue
predicted has_curve_contour: False    gt has_curve_contour: False
predicted has_edge_contour: True    gt has_edge_contour: True
predicted has_plane: True    gt has_plane: True
predicted has_rect_plane: True    gt has_rect_plane: True
predicted has_round_plane: False    gt has_round_plane: False
****************
****************
predicted shape: cone    gt shape: cone
predicted size: large    gt siz

  1%|▍                                       | 73/7676 [00:00<00:52, 144.48it/s]

...

****************
predicted shape: cylinder    gt shape: cylinder
predicted size: medium    gt size: medium
predicted color: yellow    gt color: yellow
predicted has_curve_contour: True    gt has_curve_contour: True
predicted has_edge_contour: True    gt has_edge_contour: True
predicted has_plane: True    gt has_plane: True
predicted has_rect_plane: False    gt has_rect_plane: False
predicted has_round_plane: True    gt has_round_plane: True
****************
****************
predicted shape: capsule    gt shape: capsule
predicted size: medium    gt size: medium
predicted color: yellow    gt color: yellow
predicted has_curve_contour: True    gt has_curve_contour: True
predicted has_edge_contour: True    gt has_edge_contour: True
predicted has_plane: True    gt has_plane: True
predicted has_rect_plane: False    gt has_rect_plane: False
predicted has_round_plane: False    gt has_round_plane: False
****************
****************
predicted shape: sphere    gt shape: sphere
predicted size:

100%|█████████████████████████████████████▉| 7656/7676 [00:54<00:00, 137.41it/s]

****************
predicted shape: box    gt shape: box
predicted size: small    gt size: small
predicted color: red    gt color: red
predicted has_curve_contour: False    gt has_curve_contour: False
predicted has_edge_contour: True    gt has_edge_contour: True
predicted has_plane: True    gt has_plane: True
predicted has_rect_plane: True    gt has_rect_plane: True
predicted has_round_plane: False    gt has_round_plane: False
****************
****************
predicted shape: box    gt shape: box
predicted size: small    gt size: small
predicted color: purple    gt color: purple
predicted has_curve_contour: False    gt has_curve_contour: False
predicted has_edge_contour: True    gt has_edge_contour: True
predicted has_plane: True    gt has_plane: True
predicted has_rect_plane: True    gt has_rect_plane: True
predicted has_round_plane: False    gt has_round_plane: False
****************
****************
predicted shape: capsule    gt shape: capsule
predicted size: small    gt size: small

100%|██████████████████████████████████████| 7676/7676 [00:55<00:00, 139.22it/s]

****************
predicted shape: cone    gt shape: cone
predicted size: small    gt size: small
predicted color: purple    gt color: purple
predicted has_curve_contour: True    gt has_curve_contour: True
predicted has_edge_contour: True    gt has_edge_contour: True
predicted has_plane: True    gt has_plane: True
predicted has_rect_plane: False    gt has_rect_plane: False
predicted has_round_plane: True    gt has_round_plane: True
****************
****************
predicted shape: box    gt shape: box
predicted size: small    gt size: small
predicted color: red    gt color: red
predicted has_curve_contour: False    gt has_curve_contour: False
predicted has_edge_contour: True    gt has_edge_contour: True
predicted has_plane: True    gt has_plane: True
predicted has_rect_plane: True    gt has_rect_plane: True
predicted has_round_plane: False    gt has_round_plane: False
****************
****************
predicted shape: cylinder    gt shape: cylinder
predicted size: small    gt size: sma

In [7]:
print("shape prediction accuracy = %f" % (shape_correct / test_size))
print("size prediction accuracy = %f" % (size_correct / test_size))
print("color prediction accuracy = %f" % (color_correct / test_size))
print("has_curve_contour prediction accuracy = %f" % (curve_contour_acc / test_size))
print("has_edge_contour prediction accuracy = %f" % (edge_contour_acc / test_size))
print("has_plane prediction accuracy = %f" % (plane_acc / test_size))
print("has_rect_plane prediction accuracy = %f" % (rect_plane_acc / test_size))
print("has_round_plane prediction accuracy = %f" % (round_plane_acc / test_size))

shape prediction accuracy = 0.948411
size prediction accuracy = 0.986712
color prediction accuracy = 0.951537
has_curve_contour prediction accuracy = 0.991662
has_edge_contour prediction accuracy = 0.964435
has_plane prediction accuracy = 0.962871
has_rect_plane prediction accuracy = 0.991662
has_round_plane prediction accuracy = 0.960266
